In [94]:
from current import grid, determine_directions
import pandas as pd
import numpy as np

class Locator:
    """ This module returns dataframes that could be used to analyze the board much faster """

    def __init__(self, board, ship):
        self.board = board
        self.ship = ship
        self.ship_position = ship.position
        # Get the grid
        self.grid = grid(ship.cell)

    def get_ship_info(self):
        """ Returns the info about ships in all of the board. """
        ships_info = {}

        for ship_id, ship in self.board.ships.items():
            base_info = {"my_ship": 0, "moves": 0, "position": (ship.position.x, ship.position.y),
                         'cargo': ship.cell.halite,
                         'dirX': (determine_directions(self.ship_position, ship.position))[0],
                         'dirY': (determine_directions(self.ship_position, ship.position))[1],
                         'movesX': min(abs(self.ship_position.x - ship.position.x),
                                       abs(21 - self.ship_position.x + ship.position.x)),
                         'movesY': min(abs(self.ship_position.y - ship.position.y),
                                       abs(21 - self.ship_position.y + ship.position.y))}

            base_info['moves'] = base_info['movesX'] + base_info['movesY']

            if ship_id in self.board.current_player.ship_ids and ship.id != self.ship.id:
                base_info['my_ship'] = 1
                ships_info[ship_id] = base_info
            elif not (ship_id in self.board.current_player.ship_ids):
                ships_info[ship_id] = base_info

        return pd.DataFrame(ships_info)

    def get_shipyard_info(self):
        """ Returns the info about shipyards in all of the board. """
        shipyards_info = {}

        for shipyard_id, shipyard in self.board.shipyards.items():
            base_info = {"my_shipyard": 0, "position": (shipyard.position.x, shipyard.position.y),
                         'dirX': (determine_directions(self.ship_position, shipyard.position))[0],
                         'dirY': (determine_directions(self.ship_position, shipyard.position))[1],
                         'player_halite': shipyard.player.halite,
                         'movesX': min(abs(self.ship_position.x - shipyard.position.x),
                                       abs(21 - self.ship_position.x + shipyard.position.x)),
                         'movesY': min(abs(self.ship_position.y - shipyard.position.y),
                                       abs(21 - self.ship_position.y + shipyard.position.y))}

            base_info['moves'] = base_info['movesX'] + base_info['movesY']

            if shipyard_id in self.board.current_player.shipyard_ids:
                base_info['my_shipyard'] = 1
                shipyards_info[shipyard_id] = base_info
            else:
                shipyards_info[shipyard_id] = base_info

        return pd.DataFrame(shipyards_info)

    def generate_grid_df(self):
        """ Generates a Dataframe describing the information of objects and cells in the grid of the ship. """
        all_dirs = {}

        total_moves = len(self.grid) / 4

        for direction, cell in self.grid.items():

            base_info = {
                "ship_id": None, "shipyard_id": None,
                "my_ship": 0, "my_shipyard": 0,
                "halite": 0, "moves": 0,
                "movesX": 0, "movesY": 0,
                "dirY": 'None', "dirX": 'None',
                'weightX': 0, 'weightY': 0
            }

            if "N" in direction:
                base_info['dirY'] = 'N'
                base_info['movesY'] = direction.count("N")
            elif "S" in direction:
                base_info['dirY'] = 'S'
                base_info['movesY'] = direction.count("S")

            if "W" in direction:
                base_info['dirX'] = 'W'
                base_info['movesX'] = direction.count("W")
            elif "E" in direction:
                base_info['dirX'] = 'E'
                base_info['movesX'] = direction.count("E")

            if base_info['dirY'] != 'None':
                relative = 1 / (len(direction) ** 2 * base_info['movesY']) 
                base_info['weightY'] =  relative

            if base_info['dirX'] != 'None':
                relative = 1 / (len(direction) ** 2 * base_info['movesX']) 
                base_info['weightX'] = relative

            if cell.ship is not None:
                base_info["ship_id"] = cell.ship.id
                if cell.ship.id in self.ship.player.ship_ids:
                    base_info["my_ship"] = 1

            if cell.shipyard is not None:
                base_info["shipyard_id"] = cell.shipyard.id
                if cell.shipyard.id in self.ship.player.shipyard_ids:
                    base_info['my_shipyard'] = 1

            base_info['halite'] = cell.halite
            # The number of letters in the direction would indicate the number of moves needed to get there
            base_info['moves'] = len(direction)

            all_dirs[direction] = base_info

        return pd.DataFrame(all_dirs)

In [3]:
from kaggle_environments import make
from kaggle_environments.envs.halite.helpers import *

# Create a test environment for use later
board_size = 21
environment = make("halite", configuration={"size": board_size, "startingHalite": 30000}, debug=True)
agent_count = 4
environment.reset(agent_count)
state = environment.state[0]

In [92]:
# Change the behviour of my own movement from board.current_player
board = Board(state.observation, environment.configuration)

board.current_player.ships[0].next_action = ShipAction.CONVERT
board.ships['0-2'].next_action = ShipAction.CONVERT
board.ships['0-3'].next_action = ShipAction.CONVERT
board.ships['0-4'].next_action = ShipAction.CONVERT
board = board.next()

board.current_player.shipyards[0].next_action = ShipyardAction.SPAWN
board.shipyards['1-2'].next_action = ShipyardAction.SPAWN
board.shipyards['1-3'].next_action = ShipyardAction.SPAWN
board.shipyards['1-4'].next_action = ShipyardAction.SPAWN
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.shipyards[0].next_action = ShipyardAction.SPAWN
# Opponents
board.ships['2-2'].next_action = ShipAction.NORTH
board.shipyards['1-2'].next_action = ShipyardAction.SPAWN
board.ships['2-3'].next_action = ShipAction.WEST
board.shipyards['1-3'].next_action = ShipyardAction.SPAWN
board.ships['2-4'].next_action = ShipAction.EAST
board.shipyards['1-4'].next_action = ShipyardAction.SPAWN
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.NORTH
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.shipyards[0].next_action = ShipyardAction.SPAWN
# Opponents
board.ships['2-2'].next_action = ShipAction.WEST
board.shipyards['1-2'].next_action = ShipyardAction.SPAWN
board.ships['2-3'].next_action = ShipAction.NORTH
board.shipyards['1-3'].next_action = ShipyardAction.SPAWN
board.ships['2-4'].next_action = ShipAction.SOUTH
board.shipyards['1-4'].next_action = ShipyardAction.SPAWN
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.ships[2].next_action  = ShipAction.EAST
# Opponents
board.ships['2-2'].next_action = ShipAction.WEST
board.ships['2-3'].next_action = ShipAction.EAST
board.ships['2-4'].next_action = ShipAction.SOUTH
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.ships[2].next_action  = ShipAction.EAST
# Opponents
board.ships['2-2'].next_action = ShipAction.WEST
board.ships['2-3'].next_action = ShipAction.EAST
board.ships['2-4'].next_action = ShipAction.SOUTH
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.ships[2].next_action  = ShipAction.EAST
# Opponents
board.ships['2-2'].next_action = ShipAction.WEST
board.ships['2-3'].next_action = ShipAction.EAST
board.ships['2-4'].next_action = ShipAction.SOUTH
board = board.next()

# Current-Player
board.current_player.ships[0].next_action  = ShipAction.EAST
board.current_player.ships[1].next_action  = ShipAction.SOUTH
board.current_player.ships[2].next_action  = ShipAction.EAST
# Opponents
board.ships['2-2'].next_action = ShipAction.NORTH
board.ships['2-3'].next_action = ShipAction.EAST
board.ships['2-4'].next_action = ShipAction.SOUTH
board = board.next()

board.current_player.ships[0].next_action = ShipAction.CONVERT
board = board.next()

ship = board.current_player.ships[0]

In [95]:
grid =  Locator(board, ship).generate_grid_df().T
# Checking to see if the directions are implemented properly
grid.iloc[0:65, :]

ship_id shipyard_id my_ship my_shipyard   halite moves movesX movesY  \
N        None        None       0           0  168.718     1      0      1   
S        None        None       0           0  172.092     1      0      1   
W        None        None       0           0        0     1      1      0   
E        None        None       0           0        0     1      1      0   
NW       None        None       0           0  217.507     2      1      1   
NE       None        None       0           0   62.146     2      1      1   
SW       None        None       0           0  217.507     2      1      1   
SE       None        None       0           0   62.146     2      1      1   
WW       None        None       0           0        0     2      2      0   
EE       None        None       0           0        0     2      2      0   
NN       None        None       0           0    5.858     2      0      2   
SS       None        None       0           0    5.975     2      0      2   
SSS      None        None       0           0   43.023     3      0      3   
EEE      None        None       0           0        0     3      3      0   
WWW      None        None       0           0   138.63     3      3      0   
NNN      None        None       0           0   42.179     3      0      3   
ENN      None        None       0           0        0     3      1      2   
WNN      None        None       0           0  160.142     3      1      2   
ESS      None        None       0           0        0     3      1      2   
WSS      None        None       0           0  160.142     3      1      2   
SEE      None        None       0           0        0     3      2      1   
NEE      None        None       0           0        0     3      2      1   
SWW      None        None       0           0      500     3      2      1   
NWW      None        None       0           0      500     3      2      1   
NNNN     None        None       0           0        0     4      0      4   
SSSS     None        None       0           0        0     4      0      4   
WWWW     None        None       0           0        0     4      4      0   
EEEE     None        None       0           0      500     4      4      0   
EESS     None        None       0           0        0     4      2      2   
EENN     None        None       0           0        0     4      2      2   
WWNN     None        None       0           0        0     4      2      2   
WWSS     None        None       0           0        0     4      2      2   
WWWS     None        None       0           0        0     4      3      1   
EEES     None        None       0           0   62.146     4      3      1   
EEEN     None        None       0           0   62.146     4      3      1   
WWWN     None        None       0           0        0     4      3      1   
SSSW     None        None       0           0        0     4      1      3   
SSSE     None        None       0           0   87.241     4      1      3   
NNNE     None        None       0           0   87.241     4      1      3   
NNNW     None        None       0           0        0     4      1      3   
SSSSS    None         1-3       0           0        0     5      0      5   
NNNNN    None         1-1       0           1        0     5      0      5   
WWWWW    None        None       0           0  337.017     5      5      0   
EEEEE    None        None       0           0   199.58     5      5      0   
WWWWN    None        None       0           0        0     5      4      1   
WWWWS    None        None       0           0        0     5      4      1   
EEEEN    None        None       0           0      500     5      4      1   
EEEES    None        None       0           0      500     5      4      1   
SSSSE    None        None       0           0        0     5      1      4   
SSSSW    None        None       0           0        0     5      1      4   
NNNNW    None        None   

In [4]:
print(board)

| 0 | 3 | 2 | 0 | 0 | 0 | 5 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 5 | 0 | 0 | 0 | 2 | 3 | 0 |
| 0 | 0 | 0 | 8 | 0 | 0 | 1 | 0 | 0 | 4 | 0 | 4 | 0 | 0 | 1 | 0 | 0 | 8 | 0 | 0 | 0 |
| 0 | 6 | 3 | 0 | 0 | 0 | 7 | 6 | 0 | 0 | 0 | 0 | 0 | 6 | 7 | 0 | 0 | 0 | 3 | 6 | 0 |
| 0 | 0 | 0 | 3 | 0 | 0 | 0 | 5 | 0 | 0 | 2 |b0 | 0 | 5 | 0 | 0 | 0 | 3 | 0 | 0 | 0 |
| 4 | 4 | 0 | 9 | 1 | 0 | 7 | 0 | 3 | 0 | 0A| 0 | 3 | 0 | 7 | 0 | 1 | 9 | 0 | 4 | 4 |
| 0 | 1 | 1 | 0 | 0 | 0A| 0 | 0 | 1 |a6 | 0 | 8 | 1 | 0 | 0 | 0B| 0 | 0 | 1 | 1 | 0 |
| 0 | 0 | 2 | 1 | 0 | 0 | 0 | 1 | 0 | 0 | 0 | 0 | 0 | 1 | 0 | 0 | 0 | 1 | 2 | 0 | 0 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 3 | 0 | 3 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 4 | 0 | 0 | 0 | 0 | 1 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 1 | 0 | 0 | 0 | 0 | 4 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 1 | 0 | 4 | 0 | 1 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 |
| 2 | 9 | 0 | 6 | 1 |a0 | 0 | 0 | 0 | 0 | 1 | 0 | 0 | 0 | 0 | 0 | 1 | 6 | 0 | 9 | 2 |
| 0 | 0 | 0 | 0 | 0 | 0 | 0 | 0 | 1 | 0 | 4 | 0 | 1 | 

In [46]:
grid.loc[pd.isna(grid['shipyard_id']) == False]

ship_id shipyard_id my_ship my_shipyard halite moves movesX movesY dirY  \
SSSSS    None         1-3       0           0      0     5      0      5    S   
NNNNN    None         1-1       0           1      0     5      0      5    N   

       dirX weightX    weightY  
SSSSS  None       0  0.0353757  
NNNNN  None       0  0.0353757

In [210]:
grid.iloc[1,:] == '1-1'

N         False
S         False
W         False
E         False
NW        False
          ...  
WWWSSS    False
NNNNEE    False
NNNNWW    False
SSSSWW    False
SSSSEE    False
Name: shipyard_id, Length: 84, dtype: bool

In [225]:
loc.get_shipyard_info()

1-1       1-2     1-3      1-4       9-1
my_shipyard          1         0       0        0         1
position       (5, 15)  (15, 15)  (5, 5)  (15, 5)  (10, 16)
dirX              None         E    None        E         E
dirY                 N         N       S        S         N
player_halite     2500      3000    3000     3000      2500
movesX               0        10       0       10         5
movesY               5         5       5        5         6
moves                5        15       5       15        11

In [111]:
%%writefile current.py

Overwriting current.py


In [7]:
from kaggle_environments import make
from kaggle_environments.envs.halite.helpers import *

env = make("halite", debug=True)
env.run(["random", "current.py", 'random', 'agent_a.py'])
env.render(mode="ipython", width=800, height=600)